# Data Loading and Exploration


In [6]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import accuracy_score
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from sklearn.ensemble import StackingClassifier, VotingClassifier
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import SMOTE
from sklearn.pipeline import make_pipeline
from sklearn.pipeline import Pipeline  # Import Pipeline
from sklearn.impute import SimpleImputer



import warnings
warnings.filterwarnings('ignore')



# Read the dataset


In [7]:

df = pd.read_csv('../datasets/PCOS_data.csv')


# Display basic information and the first few rows


In [8]:
print(df.info())
display(df.head())

# Generate descriptive statistics
display(df.describe())

# Check for missing values
print(df.isnull().sum())

# Normalize column names
df.columns = df.columns.str.strip().str.replace(' ', '_')
print(df.columns.tolist())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541 entries, 0 to 540
Data columns (total 44 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   Sl. No                  541 non-null    int64  
 1   Patient File No.        541 non-null    int64  
 2   PCOS (Y/N)              541 non-null    int64  
 3    Age (yrs)              541 non-null    int64  
 4   Weight (Kg)             541 non-null    float64
 5   Height(Cm)              541 non-null    float64
 6   BMI                     541 non-null    float64
 7   Blood Group             541 non-null    int64  
 8   Pulse rate(bpm)         541 non-null    int64  
 9   RR (breaths/min)        541 non-null    int64  
 10  Hb(g/dl)                541 non-null    float64
 11  Cycle(R/I)              541 non-null    int64  
 12  Cycle length(days)      541 non-null    int64  
 13  Marraige Status (Yrs)   540 non-null    float64
 14  Pregnant(Y/N)           541 non-null    in

Sl. No  Patient File No.  PCOS (Y/N)   Age (yrs)  Weight (Kg)  Height(Cm)   \
0       1                 1           0          28         44.6        152.0   
1       2                 2           0          36         65.0        161.5   
2       3                 3           1          33         68.8        165.0   
3       4                 4           0          37         65.0        148.0   
4       5                 5           0          25         52.0        161.0   

    BMI  Blood Group  Pulse rate(bpm)   RR (breaths/min)  ...  Pimples(Y/N)  \
0  19.3           15                78                22  ...             0   
1  24.9           15                74                20  ...             0   
2  25.3           11                72                18  ...             1   
3  29.7           13                72                20  ...             0   
4  20.1           11                72                18  ...             0   

   Fast food (Y/N)  Reg.Exercise(Y/N)  BP _Systolic (mmHg)  \
0              1.0                  0                  110   
1              0.0                  0                  120   
2              1.0                  0                  120   
3              0.0                  0                  120   
4              0.0                  0                  120   

   BP _Diastolic (mmHg)  Follicle No. (L)  Follicle No. (R)  \
0                    80                 3                 3   
1                    70                 3                 5   
2                    80                13                15   
3                    70                 2                 2   
4                    80                 3                 4   

  Avg. F size (L) (mm)  Avg. F size (R) (mm)  Endometrium (mm)  
0                 18.0                  18.0               8.5  
1                 15.0                  14.0               3.7  
2                 18.0                  20.0              10.0  
3                 15.0                  14.0               7.5  
4                 16.0                  14.0               7.0  

[5 rows x 44 columns]

Sl. No  Patient File No.  PCOS (Y/N)   Age (yrs)  Weight (Kg)  \
count  541.000000        541.000000  541.000000  541.000000   541.000000   
mean   271.000000        271.000000    0.327172   31.430684    59.637153   
std    156.317519        156.317519    0.469615    5.411006    11.028287   
min      1.000000          1.000000    0.000000   20.000000    31.000000   
25%    136.000000        136.000000    0.000000   28.000000    52.000000   
50%    271.000000        271.000000    0.000000   31.000000    59.000000   
75%    406.000000        406.000000    1.000000   35.000000    65.000000   
max    541.000000        541.000000    1.000000   48.000000   108.000000   

       Height(Cm)          BMI  Blood Group  Pulse rate(bpm)   \
count   541.000000  541.000000   541.000000        541.000000   
mean    156.484835   24.307579    13.802218         73.247689   
std       6.033545    4.055129     1.840812          4.430285   
min     137.000000   12.400000    11.000000         13.000000   
25%     152.000000   21.600000    13.000000         72.000000   
50%     156.000000   24.200000    14.000000         72.000000   
75%     160.000000   26.600000    15.000000         74.000000   
max     180.000000   38.900000    18.000000         82.000000   

       RR (breaths/min)  ...  Pimples(Y/N)  Fast food (Y/N)  \
count        541.000000  ...    541.000000       540.000000   
mean          19.243993  ...      0.489834         0.514815   
std            1.688629  ...      0.500359         0.500244   
min           16.000000  ...      0.000000         0.000000   
25%           18.000000  ...      0.000000         0.000000   
50%           18.000000  ...      0.000000         1.000000   
75%           20.000000  ...      1.000000         1.000000   
max           28.000000  ...      1.000000         1.000000   

       Reg.Exercise(Y/N)  BP _Systolic (mmHg)  BP _Diastolic (mmHg)  \
count         541.000000           541.000000            541.000000   
mean            0.247689           114.661738             76.927911   
std             0.432070             7.384556              5.574112   
min             0.000000            12.000000              8.000000   
25%             0.000000           110.000000             70.000000   
50%             0.000000           110.000000             80.000000   
75%             0.000000           120.000000             80.000000   
max             1.000000           140.000000            100.000000   

       Follicle No. (L)  Follicle No. (R)  Avg. F size (L) (mm)  \
count        541.000000        541.000000            541.000000   
mean           6.129390          6.641405             15.018115   
std            4.229294          4.436889              3.566839   
min            0.000000          0.000000              0.000000   
25%            3.000000          3.000000             13.000000   
50%            5.000000          6.000000             15.000000   
75%            9.000000         10.000000             18.000000   
max           22.000000         20.000000             24.000000   

       Avg. F size (R) (mm)  Endometrium (mm)  
count            541.000000        541.000000  
mean              15.451701          8.475915  
std                3.318848          2.165381  
min                0.000000          0.000000  
25%               13.000000          7.000000  
50%               16.000000          8.500000  
75%               18.000000          9.800000  
max               24.000000         18.000000  

[8 rows x 42 columns]

Sl. No                    0
Patient File No.          0
PCOS (Y/N)                0
 Age (yrs)                0
Weight (Kg)               0
Height(Cm)                0
BMI                       0
Blood Group               0
Pulse rate(bpm)           0
RR (breaths/min)          0
Hb(g/dl)                  0
Cycle(R/I)                0
Cycle length(days)        0
Marraige Status (Yrs)     1
Pregnant(Y/N)             0
No. of abortions          0
  I   beta-HCG(mIU/mL)    0
II    beta-HCG(mIU/mL)    0
FSH(mIU/mL)               0
LH(mIU/mL)                0
FSH/LH                    0
Hip(inch)                 0
Waist(inch)               0
Waist:Hip Ratio           0
TSH (mIU/L)               0
AMH(ng/mL)                0
PRL(ng/mL)                0
Vit D3 (ng/mL)            0
PRG(ng/mL)                0
RBS(mg/dl)                0
Weight gain(Y/N)          0
hair growth(Y/N)          0
Skin darkening (Y/N)      0
Hair loss(Y/N)            0
Pimples(Y/N)              0
Fast food (Y/N)     

# Data Preprocessing


In [9]:
# Normalize column names
df.columns = df.columns.str.strip().str.replace(' ', '_')

# Handle numeric columns (coerce non-numeric to NaN)
numeric_columns = ['BMI', 'Age_(yrs)', 'Weight_(Kg)', 'Waist:Hip_Ratio', 'I___beta-HCG(mIU/mL)', 
                   'II____beta-HCG(mIU/mL)', 'FSH(mIU/mL)', 'LH(mIU/mL)', 'AMH(ng/mL)', 
                   'Cycle_length(days)', 'Endometrium_(mm)', 'BP__Systolic_(mmHg)', 'BP__Diastolic_(mmHg)']

for col in numeric_columns:
    df[col] = pd.to_numeric(df[col].replace(r'^\.+$', '', regex=True), errors='coerce')
    
# Impute missing values in numeric columns with the median
imputer = SimpleImputer(strategy='median')
df[numeric_columns] = imputer.fit_transform(df[numeric_columns])

# Fill the single missing value in 'Marraige_Status_(Yrs)' with the median
df['Marraige_Status_(Yrs)'].fillna(df['Marraige_Status_(Yrs)'].median(), inplace=True)

# Handle categorical columns and fill missing values with mode
categorical_columns = ['PCOS_(Y/N)', 'Pregnant(Y/N)', 'Weight_gain(Y/N)', 'hair_growth(Y/N)', 
                       'Skin_darkening_(Y/N)', 'Hair_loss(Y/N)', 'Pimples(Y/N)', 
                       'Fast_food_(Y/N)', 'Reg.Exercise(Y/N)', 'Blood_Group']

for col in categorical_columns:
    df[col] = df[col].fillna(df[col].mode()[0])

# Encode categorical columns
labelencoder = LabelEncoder()
df[categorical_columns] = df[categorical_columns].apply(labelencoder.fit_transform)


# Split the dataset


In [10]:
X = df.drop('PCOS_(Y/N)', axis=1)
y = df['PCOS_(Y/N)']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)


# Define preprocessing pipeline (imputation + scaling)


In [11]:
# Define preprocessing pipeline (imputation + scaling)
pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy='median')),  # Impute missing values with median
    ('scaler', StandardScaler())                   # Standard scaling of features
])

# Preprocess the training and test sets


In [12]:
# Preprocess the training and test sets
X_train_preprocessed = pipeline.fit_transform(X_train)
X_test_preprocessed = pipeline.transform(X_test)


# Apply SMOTE only on the preprocessed training data


In [13]:
# Apply SMOTE only on the preprocessed training data
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_train_preprocessed, y_train)


In [14]:
# Display the class distribution after SMOTE
print(f"Class distribution after SMOTE:\n{pd.Series(y_resampled).value_counts()}")


Class distribution after SMOTE:
PCOS_(Y/N)
0    291
1    291
Name: count, dtype: int64


# Model Training 

In [15]:
# Define classifiers
classifiers = {
    'KNN (k=3)': KNeighborsClassifier(n_neighbors=3),
    'KNN (k=5)': KNeighborsClassifier(n_neighbors=5),
    'Decision Tree (gini)': DecisionTreeClassifier(criterion='gini'),
    'Decision Tree (entropy)': DecisionTreeClassifier(criterion='entropy'),
    'Random Forest': RandomForestClassifier(n_estimators=100, random_state=42),
    'Naive Bayes': GaussianNB(),
    'Dummy Classifier': DummyClassifier(strategy='most_frequent'),
    'XGBoost': XGBClassifier(use_label_encoder=False, eval_metric='logloss', random_state=42),
    'LightGBM': LGBMClassifier(random_state=42),
    'CatBoost': CatBoostClassifier(verbose=0, random_state=42)
}


In [16]:
# Train and evaluate classifiers
results = {}
for name, clf in classifiers.items():
    clf.fit(X_resampled, y_resampled)  # Use resampled training data
    y_pred = clf.predict(X_test_preprocessed)
    accuracy = accuracy_score(y_test, y_pred)
    results[name] = accuracy
    print(f'{name} - Accuracy: {accuracy:.4f}')


KNN (k=3) - Accuracy: 0.8532
KNN (k=5) - Accuracy: 0.8807
Decision Tree (gini) - Accuracy: 0.8349
Decision Tree (entropy) - Accuracy: 0.8807
Random Forest - Accuracy: 0.9266
Naive Bayes - Accuracy: 0.7890
Dummy Classifier - Accuracy: 0.6697
XGBoost - Accuracy: 0.9266
[LightGBM] [Info] Number of positive: 291, number of negative: 291
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000243 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3611
[LightGBM] [Info] Number of data points in the train set: 582, number of used features: 43
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

# Display the results


In [17]:
# Display the results
results_df = pd.DataFrame(list(results.items()), columns=['Classifier', 'Accuracy'])
print(results_df.sort_values(by='Accuracy', ascending=False))


                Classifier  Accuracy
4            Random Forest  0.926606
7                  XGBoost  0.926606
8                 LightGBM  0.917431
9                 CatBoost  0.917431
1                KNN (k=5)  0.880734
3  Decision Tree (entropy)  0.880734
0                KNN (k=3)  0.853211
2     Decision Tree (gini)  0.834862
5              Naive Bayes  0.788991
6         Dummy Classifier  0.669725


In [21]:
import optuna
from sklearn.model_selection import StratifiedKFold, cross_val_score
from sklearn.ensemble import RandomForestClassifier

# Define cross-validation method


In [22]:
# Define cross-validation method
cv = StratifiedKFold(n_splits=5)

# Hyperparameter tuning


Decision Tree

In [23]:
# Hyperparameter tuning for Decision Tree
def dt_objective(trial):
    params = {
        'criterion': trial.suggest_categorical('criterion', ['gini', 'entropy']),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 10),
    }
    dt = DecisionTreeClassifier(**params, random_state=42)
    score = cross_val_score(dt, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
    return score

study_dt = optuna.create_study(direction='maximize')
study_dt.optimize(dt_objective, n_trials=50)
best_dt_params = study_dt.best_trial.params
print(f"Best Decision Tree params: {best_dt_params}")

[I 2024-10-15 17:03:22,533] A new study created in memory with name: no-name-3ce2dc9c-3381-4ca1-8634-392214ef5774
[I 2024-10-15 17:03:22,559] Trial 0 finished with value: 0.848894783377542 and parameters: {'criterion': 'entropy', 'max_depth': 4, 'min_samples_split': 5, 'min_samples_leaf': 5}. Best is trial 0 with value: 0.848894783377542.
[I 2024-10-15 17:03:22,585] Trial 1 finished with value: 0.873017978190392 and parameters: {'criterion': 'entropy', 'max_depth': 14, 'min_samples_split': 6, 'min_samples_leaf': 4}. Best is trial 1 with value: 0.873017978190392.
[I 2024-10-15 17:03:22,611] Trial 2 finished with value: 0.8712938402593575 and parameters: {'criterion': 'entropy', 'max_depth': 15, 'min_samples_split': 9, 'min_samples_leaf': 8}. Best is trial 1 with value: 0.873017978190392.
[I 2024-10-15 17:03:22,636] Trial 3 finished with value: 0.8576186265841439 and parameters: {'criterion': 'gini', 'max_depth': 14, 'min_samples_split': 4, 'min_samples_leaf': 2}. Best is trial 1 with va

Best Decision Tree params: {'criterion': 'entropy', 'max_depth': 12, 'min_samples_split': 6, 'min_samples_leaf': 1}


XGBoost

In [24]:
# Hyperparameter tuning for XGBoost
def xgb_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0)
    }
    xgb = XGBClassifier(**params, use_label_encoder=False, eval_metric='logloss', random_state=42)
    score = cross_val_score(xgb, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
    return score

study_xgb = optuna.create_study(direction='maximize')
study_xgb.optimize(xgb_objective, n_trials=50)
best_xgb_params = study_xgb.best_trial.params
print(f"Best XGBoost params: {best_xgb_params}")

[I 2024-10-15 17:03:34,067] A new study created in memory with name: no-name-d9bae865-f65b-4292-b61b-82a2f7ee5eac
[I 2024-10-15 17:03:34,790] Trial 0 finished with value: 0.9159593280282936 and parameters: {'n_estimators': 320, 'max_depth': 6, 'learning_rate': 0.037439734530466534, 'subsample': 0.5463890901293114, 'colsample_bytree': 0.5226242419435136}. Best is trial 0 with value: 0.9159593280282936.
[I 2024-10-15 17:03:35,937] Trial 1 finished with value: 0.922826407309166 and parameters: {'n_estimators': 450, 'max_depth': 5, 'learning_rate': 0.014809595173335584, 'subsample': 0.9116657018238024, 'colsample_bytree': 0.9733492812515372}. Best is trial 1 with value: 0.922826407309166.
[I 2024-10-15 17:03:36,269] Trial 2 finished with value: 0.9125405246094902 and parameters: {'n_estimators': 226, 'max_depth': 3, 'learning_rate': 0.1620805701415618, 'subsample': 0.5366956796796892, 'colsample_bytree': 0.7658875218515628}. Best is trial 1 with value: 0.922826407309166.
[I 2024-10-15 17:0

Best XGBoost params: {'n_estimators': 301, 'max_depth': 7, 'learning_rate': 0.1339132196456812, 'subsample': 0.7307670243057154, 'colsample_bytree': 0.8481798842456956}


LightGBM

In [25]:
# Hyperparameter tuning for LightGBM
def lgbm_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 150),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0)
    }
    lgbm = LGBMClassifier(**params, random_state=42)
    score = cross_val_score(lgbm, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
    return score

study_lgbm = optuna.create_study(direction='maximize')
study_lgbm.optimize(lgbm_objective, n_trials=50)
best_lgbm_params = study_lgbm.best_trial.params
print(f"Best LightGBM params: {best_lgbm_params}")

[I 2024-10-15 17:03:59,794] A new study created in memory with name: no-name-f4a79b84-2649-4279-919e-01ff5a6b1df3


[LightGBM] [Info] Number of positive: 233, number of negative: 232
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000372 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3089
[LightGBM] [Info] Number of data points in the train set: 465, number of used features: 43
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.501075 -> initscore=0.004301
[LightGBM] [Info] Start training from score 0.004301
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

[I 2024-10-15 17:04:00,107] Trial 0 finished with value: 0.9227969348659004 and parameters: {'n_estimators': 491, 'max_depth': 4, 'learning_rate': 0.2463802831204772, 'num_leaves': 148, 'subsample': 0.5671355579303808}. Best is trial 0 with value: 0.9227969348659004.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 17:04:00,415] Trial 1 finished with value: 0.9331122900088417 and parameters: {'n_estimators': 434, 'max_depth': 5, 'learning_rate': 0.21177786800557696, 'num_leaves': 101, 'subsample': 0.8450801631022764}. Best is trial 1 with value: 0.9331122900088417.
[I 2024-10-15 17:04:00,604] Trial 2 finished with value: 0.9194076038903625 and parameters: {'n_estimators': 155, 'max_depth': 7, 'learning_rate': 0.23656625160099828, 'num_leaves': 70, 'subsample': 0.9059163980405882}. Best is trial 1 with value: 0.9331122900088417.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 17:04:15,369] Trial 48 finished with value: 0.9296787503684056 and parameters: {'n_estimators': 485, 'max_depth': 8, 'learning_rate': 0.12320893525827502, 'num_leaves': 141, 'subsample': 0.5828924967335557}. Best is trial 14 with value: 0.9348364279398762.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-10-15 17:04:15,637] Trial 49 finished with value: 0.9296787503684056 and parameters: {'n_estimators': 319, 'max_depth': 5, 'learning_rate': 0.1647083397921142, 'num_leaves': 112, 'subsample': 0.8871232450727171}. Best is trial 14 with value: 0.9348364279398762.


[LightGBM] [Info] Number of positive: 233, number of negative: 233
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000165 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2749
[LightGBM] [Info] Number of data points in the train set: 466, number of used features: 43
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits wit

CatBoost

In [26]:
# Hyperparameter tuning for CatBoost
def catboost_objective(trial):
    params = {
        'iterations': trial.suggest_int('iterations', 100, 500),
        'depth': trial.suggest_int('depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-5, 10),
    }
    catboost = CatBoostClassifier(**params, verbose=0, random_state=42)
    score = cross_val_score(catboost, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
    return score

study_catboost = optuna.create_study(direction='maximize')
study_catboost.optimize(catboost_objective, n_trials=50)
best_catboost_params = study_catboost.best_trial.params
print(f"Best CatBoost params: {best_catboost_params}")

[I 2024-10-15 17:04:52,473] A new study created in memory with name: no-name-42aa1145-7216-420e-9e20-bbb957f0bea7
[I 2024-10-15 17:04:53,677] Trial 0 finished with value: 0.922811671087533 and parameters: {'iterations': 271, 'depth': 3, 'learning_rate': 0.2548115805989677, 'l2_leaf_reg': 6.987159567332204}. Best is trial 0 with value: 0.922811671087533.
[I 2024-10-15 17:04:54,801] Trial 1 finished with value: 0.9245063365753021 and parameters: {'iterations': 212, 'depth': 4, 'learning_rate': 0.0870348933142444, 'l2_leaf_reg': 2.3302598026919554}. Best is trial 1 with value: 0.9245063365753021.
[I 2024-10-15 17:04:55,791] Trial 2 finished with value: 0.9313881520778071 and parameters: {'iterations': 197, 'depth': 4, 'learning_rate': 0.27777813671265655, 'l2_leaf_reg': 2.8046743133751897}. Best is trial 2 with value: 0.9313881520778071.
[I 2024-10-15 17:04:56,795] Trial 3 finished with value: 0.9313734158561744 and parameters: {'iterations': 186, 'depth': 4, 'learning_rate': 0.1219756391

Best CatBoost params: {'iterations': 210, 'depth': 5, 'learning_rate': 0.23782103801233156, 'l2_leaf_reg': 6.494610445280222}


 Random Forest

In [27]:
# Hyperparameter tuning for Random Forest
def rf_objective(trial):
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 10),
        'bootstrap': trial.suggest_categorical('bootstrap', [True, False])
    }
    rf = RandomForestClassifier(**params, random_state=42)
    score = cross_val_score(rf, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
    return score

study_rf = optuna.create_study(direction='maximize')
study_rf.optimize(rf_objective, n_trials=50)
best_rf_params = study_rf.best_trial.params
print(f"Best Random Forest params: {best_rf_params}")

[I 2024-10-15 17:07:10,416] A new study created in memory with name: no-name-b964e635-374f-4b5a-9d05-40b68bb17a9f
[I 2024-10-15 17:07:11,866] Trial 0 finished with value: 0.9297082228116711 and parameters: {'n_estimators': 326, 'max_depth': 6, 'min_samples_split': 2, 'min_samples_leaf': 2, 'bootstrap': False}. Best is trial 0 with value: 0.9297082228116711.
[I 2024-10-15 17:07:12,864] Trial 1 finished with value: 0.917683465959328 and parameters: {'n_estimators': 235, 'max_depth': 8, 'min_samples_split': 10, 'min_samples_leaf': 7, 'bootstrap': False}. Best is trial 0 with value: 0.9297082228116711.
[I 2024-10-15 17:07:14,132] Trial 2 finished with value: 0.9142499263188919 and parameters: {'n_estimators': 301, 'max_depth': 12, 'min_samples_split': 8, 'min_samples_leaf': 7, 'bootstrap': False}. Best is trial 0 with value: 0.9297082228116711.
[I 2024-10-15 17:07:14,745] Trial 3 finished with value: 0.9176539935160625 and parameters: {'n_estimators': 160, 'max_depth': 13, 'min_samples_spl

Best Random Forest params: {'n_estimators': 136, 'max_depth': 10, 'min_samples_split': 2, 'min_samples_leaf': 1, 'bootstrap': False}


In [28]:
# Final model training with the best parameters from hyperparameter tuning
dt_best = DecisionTreeClassifier(**best_dt_params, random_state=42)
xgb_best = XGBClassifier(**best_xgb_params, use_label_encoder=False, eval_metric='logloss', random_state=42)
lgbm_best = LGBMClassifier(**best_lgbm_params, random_state=42)
catboost_best = CatBoostClassifier(**best_catboost_params, verbose=0, random_state=42)
rf_best = RandomForestClassifier(**best_rf_params, random_state=42)


# Cross-validation for evaluation with tuned models

In [29]:
# Cross-validation for evaluation with tuned models
dt_score = cross_val_score(dt_best, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
xgb_score = cross_val_score(xgb_best, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
lgbm_score = cross_val_score(lgbm_best, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
catboost_score = cross_val_score(catboost_best, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()
rf_score = cross_val_score(rf_best, X_resampled, y_resampled, cv=cv, scoring='accuracy').mean()


[LightGBM] [Info] Number of positive: 233, number of negative: 232
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000181 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3089
[LightGBM] [Info] Number of data points in the train set: 465, number of used features: 43
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.501075 -> initscore=0.004301
[LightGBM] [Info] Start training from score 0.004301
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

# final results

In [30]:

print(f"Decision Tree Final Cross-Validation Accuracy: {dt_score:.4f}")
print(f"XGBoost Final Cross-Validation Accuracy: {xgb_score:.4f}")
print(f"LightGBM Final Cross-Validation Accuracy: {lgbm_score:.4f}")
print(f"CatBoost Final Cross-Validation Accuracy: {catboost_score:.4f}")
print(f"Random Forest Final Cross-Validation Accuracy: {rf_score:.4f}")

Decision Tree Final Cross-Validation Accuracy: 0.8833
XGBoost Final Cross-Validation Accuracy: 0.9297
LightGBM Final Cross-Validation Accuracy: 0.9348
CatBoost Final Cross-Validation Accuracy: 0.9349
Random Forest Final Cross-Validation Accuracy: 0.9314


In [ ]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
import time

# Initialize dictionary to store all metrics
evaluation_results = []

# Evaluate each classifier and calculate metrics
for name, clf in classifiers.items():
    start_time = time.perf_counter()  # Start timer
    clf.fit(X_resampled, y_resampled)  # Train the model
    y_pred = clf.predict(X_test_preprocessed)  # Predict on the test set
    end_time = time.perf_counter()  # End timer

    # Calculate metrics
    accuracy = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred, average='macro', zero_division=0)
    recall = recall_score(y_test, y_pred, average='macro', zero_division=0)
    f1 = f1_score(y_test, y_pred, average='macro', zero_division=0)
    time_taken = end_time - start_time

    # Append results to the list
    evaluation_results.append({
        'Classifier': name,
        'Accuracy': accuracy,
        'Precision': precision,
        'Recall': recall,
        'F1 Score': f1,
        'Time Taken (seconds)': time_taken
    })

# Convert results to a DataFrame
results_df = pd.DataFrame(evaluation_results)

# Sort by Accuracy (or any other metric)
results_df = results_df.sort_values(by='Accuracy', ascending=False)

# Display the results
print(results_df)


                Classifier  Accuracy  Precision    Recall  F1 Score  \
4            Random Forest  0.926606   0.929789  0.902968  0.914510   
7                  XGBoost  0.926606   0.929789  0.902968  0.914510   
8                 LightGBM  0.917431   0.922870  0.889079  0.903034   
9                 CatBoost  0.917431   0.915072  0.896119  0.904581   
1                KNN (k=5)  0.880734   0.864276  0.903919  0.873539   
3  Decision Tree (entropy)  0.862385   0.845946  0.840944  0.843346   
0                KNN (k=3)  0.853211   0.832867  0.862253  0.842029   
2     Decision Tree (gini)  0.853211   0.837059  0.827055  0.831660   
5              Naive Bayes  0.788991   0.784535  0.821347  0.781639   
6         Dummy Classifier  0.669725   0.334862  0.500000  0.401099   

   Time Taken (seconds)  
4              0.123040  
7              0.046196  
8              0.049433  
9              1.783315  
1              0.011086  
3              0.006524  
0              0.012690  
2              0.006006  
5              0.000555  
6              0.000133

In [ ]:
from sklearn.model_selection import StratifiedKFold, cross_val_score

# Initialize dictionary for cross-validation results
cv_results = []

# Cross-validation setup
cv = StratifiedKFold(n_splits=5)

# Perform cross-validation for each classifier
for name, clf in classifiers.items():
    start_time = time.perf_counter()
    scores = cross_val_score(clf, X_resampled, y_resampled, cv=cv, scoring='accuracy')
    end_time = time.perf_counter()

    # Calculate mean accuracy and time taken
    mean_accuracy = scores.mean()
    time_taken = end_time - start_time

    # Append results to the list
    cv_results.append({
        'Classifier': name,
        'CV Mean Accuracy': mean_accuracy,
        'Time Taken (seconds)': time_taken
    })

# Convert to DataFrame and display results
cv_results_df = pd.DataFrame(cv_results).sort_values(by='CV Mean Accuracy', ascending=False)
print("\nCross-Validation Results:")
print(cv_results_df)


Cross-Validation Results:
                Classifier  CV Mean Accuracy  Time Taken (seconds)
4            Random Forest          0.931418              0.457998
8                 LightGBM          0.926260              0.213678
9                 CatBoost          0.926260              8.211299
7                  XGBoost          0.910816              0.242083
0                KNN (k=3)          0.893634              0.045759
3  Decision Tree (entropy)          0.878146              0.026417
1                KNN (k=5)          0.874786              0.039173
2     Decision Tree (gini)          0.864486              0.027069
5              Naive Bayes          0.828235              0.005399
6         Dummy Classifier          0.498291              0.003393

In [ ]:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from scipy.stats import randint, uniform

# Define hyperparameter grids and distributions
param_grid = {
    'KNN (k=3)': {'n_neighbors': [3, 5, 7, 10]},
    'KNN (k=5)': {'n_neighbors': [3, 5, 7, 10]},
    'Decision Tree (gini)': {'max_depth': [None, 10, 20, 30], 'criterion': ['gini']},
    'Decision Tree (entropy)': {'max_depth': [None, 10, 20, 30], 'criterion': ['entropy']},
    'Random Forest': {'n_estimators': [50, 100, 200], 'max_depth': [None, 10, 20]},
    'XGBoost': {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.1, 0.2], 'max_depth': [3, 5, 7]},
    'LightGBM': {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.1, 0.2], 'num_leaves': [31, 62]},
    'CatBoost': {'iterations': [50, 100, 200], 'learning_rate': [0.01, 0.1, 0.2], 'depth': [4, 6, 8]}
}

param_dist = {
    'KNN (k=3)': {'n_neighbors': randint(1, 20)},
    'KNN (k=5)': {'n_neighbors': randint(1, 20)},
    'Decision Tree (gini)': {'max_depth': [None, 10, 20, 30], 'criterion': ['gini', 'entropy']},
    'Decision Tree (entropy)': {'max_depth': [None, 10, 20, 30], 'criterion': ['gini', 'entropy']},
    'Random Forest': {'n_estimators': randint(10, 300), 'max_depth': [None, 10, 20, 30]},
    'XGBoost': {'n_estimators': randint(50, 300), 'learning_rate': uniform(0.01, 0.2), 'max_depth': randint(3, 10)},
    'LightGBM': {'n_estimators': randint(50, 300), 'learning_rate': uniform(0.01, 0.2), 'num_leaves': randint(20, 100)},
    'CatBoost': {'iterations': randint(10, 300), 'learning_rate': uniform(0.01, 0.2), 'depth': randint(3, 10)}
}

# Initialize results for both searches
grid_search_results = []
random_search_results = []

# Perform hyperparameter tuning
for name, clf in classifiers.items():
    if name in param_grid:
        # Grid Search
        grid_search = GridSearchCV(clf, param_grid[name], cv=3, scoring='accuracy', verbose=1)
        grid_search.fit(X_resampled, y_resampled)
        grid_search_results.append({
            'Classifier': name,
            'Best Params': grid_search.best_params_,
            'Best Accuracy': grid_search.best_score_
        })

        # Randomized Search
        random_search = RandomizedSearchCV(clf, param_distributions=param_dist[name], n_iter=20, cv=3, scoring='accuracy', random_state=42, verbose=1)
        random_search.fit(X_resampled, y_resampled)
        random_search_results.append({
            'Classifier': name,
            'Best Params': random_search.best_params_,
            'Best Accuracy': random_search.best_score_
        })

# Convert to DataFrames and display
grid_search_df = pd.DataFrame(grid_search_results)
random_search_df = pd.DataFrame(random_search_results)

print("\nGrid Search Results:")
print(grid_search_df)

print("\nRandomized Search Results:")
print(random_search_df)


Grid Search Results:
                Classifier                                        Best Params  \
0                KNN (k=3)                                 {'n_neighbors': 3}   
1                KNN (k=5)                                 {'n_neighbors': 3}   
2     Decision Tree (gini)             {'criterion': 'gini', 'max_depth': 10}   
3  Decision Tree (entropy)          {'criterion': 'entropy', 'max_depth': 30}   
4            Random Forest             {'max_depth': 10, 'n_estimators': 100}   
5                  XGBoost  {'learning_rate': 0.1, 'max_depth': 3, 'n_esti...   
6                 LightGBM  {'learning_rate': 0.1, 'n_estimators': 50, 'nu...   
7                 CatBoost  {'depth': 6, 'iterations': 200, 'learning_rate...   

   Best Accuracy  
0       0.883162  
1       0.883162  
2       0.871134  
3       0.883162  
4       0.924399  
5       0.915808  
6       0.915808  
7       0.934708  

Randomized Search Results:
                Classifier                                        Best Params  \
0                KNN (k=3)                                 {'n_neighbors': 1}   
1                KNN (k=5)                                 {'n_neighbors': 1}   
2     Decision Tree (gini)          {'max_depth': 20, 'criterion': 'entropy'}   
3  Decision Tree (entropy)          {'max_depth': 30, 'criterion': 'entropy'}   
4            Random Forest              {'max_depth': 20, 'n_estimators': 97}   
5                  XGBoost  {'learning_rate': 0.15639878836228102, 'max_de...   
6                 LightGBM  {'learning_rate': 0.08327236865873834, 'n_esti...   
7                 CatBoost  {'depth': 6, 'iterations': 280, 'learning_rate...   

   Best Accuracy  
0       0.903780  
1       0.903780  
2       0.893471  
3       0.884880  
4       0.926117  
5       0.915808  
6       0.919244  
7       0.927835  

In [ ]:
final_results = []

for model_info in grid_search_results + random_search_results:
    name = model_info['Classifier']
    params = model_info['Best Params']

    # Create a new instance of the model with the best parameters
    if "CatBoost" in name:
        clf = CatBoostClassifier(**params, verbose=0, random_state=42)
    elif "XGBoost" in name:
        clf = XGBClassifier(**params, use_label_encoder=False, eval_metric='logloss', random_state=42)
    elif "LightGBM" in name:
        clf = LGBMClassifier(**params, random_state=42)
    elif "Random Forest" in name:
        clf = RandomForestClassifier(**params, random_state=42)
    elif "Decision Tree" in name:
        clf = DecisionTreeClassifier(**params, random_state=42)
    elif "KNN" in name:
        clf = KNeighborsClassifier(**params)
    elif "Naive Bayes" in name:
        clf = GaussianNB()
    elif "Dummy" in name:
        clf = DummyClassifier(**params)
    else:
        continue

    # Train and evaluate the model
    start_time = time.perf_counter()
    clf.fit(X_resampled, y_resampled)
    y_pred = clf.predict(X_test_preprocessed)
    end_time = time.perf_counter()

    # Calculate metrics
    accuracy = accuracy_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred, average='macro', zero_division=0)
    recall = recall_score(y_test, y_pred, average='macro', zero_division=0)
    f1 = f1_score(y_test, y_pred, average='macro', zero_division=0)
    time_taken = end_time - start_time

    final_results.append({
        'Classifier': name,
        'Accuracy': accuracy,
        'Precision': precision,
        'Recall': recall,
        'F1 Score': f1,
        'Time Taken (seconds)': time_taken
    })

# Convert to DataFrame and display
final_results_df = pd.DataFrame(final_results).sort_values(by='Accuracy', ascending=False)
print("\nFinal Results:")
print(final_results_df)


Final Results:
                 Classifier  Accuracy  Precision    Recall  F1 Score  \
6                  LightGBM  0.926606   0.922549  0.910008  0.915830   
12            Random Forest  0.926606   0.929789  0.902968  0.914510   
13                  XGBoost  0.926606   0.929789  0.902968  0.914510   
4             Random Forest  0.917431   0.915072  0.896119  0.904581   
7                  CatBoost  0.917431   0.915072  0.896119  0.904581   
5                   XGBoost  0.908257   0.907670  0.882230  0.893137   
14                 LightGBM  0.908257   0.901176  0.889269  0.894788   
15                 CatBoost  0.899083   0.888031  0.882420  0.885120   
3   Decision Tree (entropy)  0.871560   0.852483  0.861872  0.856794   
8                 KNN (k=3)  0.871560   0.852483  0.861872  0.856794   
9                 KNN (k=5)  0.871560   0.852483  0.861872  0.856794   
10     Decision Tree (gini)  0.871560   0.852483  0.861872  0.856794   
11  Decision Tree (entropy)  0.871560   0.852483  0.861872  0.856794   
0                 KNN (k=3)  0.853211   0.832867  0.862253  0.842029   
1                 KNN (k=5)  0.853211   0.832867  0.862253  0.842029   
2      Decision Tree (gini)  0.853211   0.832283  0.841134  0.836336   

    Time Taken (seconds)  
6               0.027233  
12              0.111890  
13              0.054412  
4               0.119388  
7               0.391472  
5               0.038196  
14              0.111108  
15              0.496564  
3               0.007931  
8               0.009547  
9               0.011342  
10              0.006300  
11              0.006185  
0               0.011697  
1               0.011528  
2               0.006733  